# 01 - Create test subset in Brat Standoff format

In [1]:
import os

os.environ["CUDA_VISIBLE_DEVICES"] = "1" #Numéro GPU
print(os.environ["CUDA_VISIBLE_DEVICES"])

1


In [2]:
import os, sys
from pathlib import Path

ENV_IS_GOOGLE_COLAB = True if 'google.colab' in str(get_ipython()) else False
os.environ["ENV_IS_GOOGLE_COLAB"] = str(ENV_IS_GOOGLE_COLAB)

if ENV_IS_GOOGLE_COLAB:
  from google.colab import drive
  mountpoint = Path("/content/drive")
  drive.mount(str(mountpoint)) # Mount gdrive to BASE
  base = mountpoint / "MyDrive/article_icdar_2023" # Adapt this to your situation
  sys.path.append(str(base)) # Add BASE to Python Path
  BASE = Path(base).resolve() # Make BASE absolute
  DATASETS =  BASE / "dataset"
else:
  BASE = Path(os.path.dirname(os.path.realpath("__file__"))).resolve() # If not on GColab, BASE will be the directory of this notebook
  DATASETS = Path('/work/stual/dataset_ICDAR').resolve()
  OUT_BASE = Path('/work/stual/res_ICDAR/method_2').resolve()

print(sys.path)
print(BASE)
print(DATASETS)
print(OUT_BASE)

['/lrde/home2/stual/stage_DAS/t1_dataset_tools', '/usr/lib/python310.zip', '/usr/lib/python3.10', '/usr/lib/python3.10/lib-dynload', '', '/lrde/home2/stual/.venv/python_3_9/lib/python3.10/site-packages']
/lrde/home2/stual/stage_DAS/t1_dataset_tools
/work/stual/dataset_ICDAR
/work/stual/res_ICDAR/method_2


In [3]:
CREATE_REF_IO = True
CREATE_REF_IOB2 = False
CREATE_PERO_IO = True
CREATE_PERO_IOB2 = False

In [4]:
MODEL_NAME = 'dalembert'
#'camembert_ner''
#pretrained_camembert_ner

In [5]:
import glob
import re
import json
import pandas as pd
import config
import os
from pathlib import Path

config.SPLIT_SEED = 42 # Random seed used in train/dev/test. Do not change it if you want to recreate the paper results.
config.DEBUG = False # If true, text versions of the spacy datasets will be saved along with the .spacy files.

## 01.1 Reference data

In [6]:
#Sanity check
DATA = DATASETS / "51-brat_ner_ref_from_pero/"
f = open(f"{DATA}/all_brat.json")
data = json.load(f)
f.close()

In [7]:
gold_reference = pd.DataFrame.from_records(data)
gold_reference

id                                                box  \
0     290  [125.49036875669651, 357.68003651377927, 386.0...   
1     292  [127.0, 398.61236450520784, 387.0, 40.38763549...   
2     294  [124.46245769617323, 436.6867055467269, 388.52...   
3     298  [122.96782088243424, 476.6769851466119, 388.0,...   
4     312   [126.68533584543587, 648.8951119484786, 393, 29]   
...   ...                                                ...   
8440  343                       [269.0, 1266.0, 405.0, 26.0]   
8441  345                       [267.0, 1293.0, 627.0, 26.0]   
8442  347                               [267, 1321, 478, 26]   
8443  349                               [267, 1349, 383, 25]   
8444  351                               [267, 1377, 444, 26]   

                               book  page  valid_box  \
0                      Bottin1_1820   107       True   
1                      Bottin1_1820   107       True   
2                      Bottin1_1820   107       True   
3                      Bottin1_1820   107       True   
4                      Bottin1_1820   107       True   
...                             ...   ...        ...   
8440  Notables_communaux_seine_1801   144       True   
8441  Notables_communaux_seine_1801   144       True   
8442  Notables_communaux_seine_1801   144       True   
8443  Notables_communaux_seine_1801   144       True   
8444  Notables_communaux_seine_1801   144       True   

                                               text_ocr  \
0     Dufant (Victor), libraire, r. du Gros-Che-\nne...   
1     Dufay, essayeur du commerce, place Dau-\nphine...   
2     Dulay, chandronnier, r. du Pont- aux\nChoux, 1...   
3     Dufay (V.e), grenetière, r. du Faub.-S.\nDenis...   
4             Dufeu, charcutier, r. Montmartre, 89. 318   
...                                                 ...   
8440                 Lamarche, géographe , rue du foin.   
8441  Lamarck, membre de l'institut, quatrième munic...   
8442           Lamare, notaire, rue du faubourg honoré.   
8443                 Lamarre , carrier, rue mouffetard.   
8444            Lamarre, clerc de notaire, rue égalité.   

                                                ner_xml  \
0     <PER>Dufant (Victor)</PER>, <ACT>libraire</ACT...   
1     <PER>Dufay</PER>, <ACT>essayeur du commerce</A...   
2     <PER>Dulay</PER>, <ACT>chandronnier</ACT>, <LO...   
3     <PER>Dufay (V.e)</PER>, <ACT>grenetière</ACT>,...   
4     <PER>Dufeu</PER>, <ACT>charcutier</ACT>, <LOC>...   
...                                                 ...   
8440  <PER>Lamarche</PER>, <ACT>géographe</ACT> , <L...   
8441  <PER>Lamarck</PER>, <ACT>membre de l&apos;inst...   
8442  <PER>Lamare</PER>, <ACT>notaire</ACT>, <LOC>ru...   
8443  <PER>Lamarre</PER> , <ACT>carrier</ACT>, <LOC>...   
8444  <PER>Lamarre</PER>, <ACT>clerc de notaire</ACT...   

                                         nested_ner_xml  \
0     <PER>Dufant (Victor)</PER>, <ACT>libraire</ACT...   
1     <PER>Dufay</PER>, <ACT>essayeur du commerce</A...   
2     <PER>Dulay</PER>, <ACT>chandronnier</ACT>, <SP...   
3     <PER>Dufay (V.e)</PER>, <ACT>grenetière</ACT>,...   
4     <PER>Dufeu</PER>, <ACT>charcutier</ACT>, <SPAT...   
...                                                 ...   
8440  <PER>Lamarche</PER>, <ACT>géographe</ACT> , <S...   
8441  <PER>Lamarck</PER>, <ACT>membre de l'institut<...   
8442  <PER>Lamare</PER>, <ACT>notaire</ACT>, <SPAT><...   
8443  <PER>Lamarre</PER> , <ACT>carrier</ACT>, <SPAT...   
8444  <PER>Lamarre</PER>, <ACT>clerc de notaire</ACT...   

                                                   brat  
0     [Dufant (Victor), libraire, r. du Gros-Che-
ne...  
1     [Dufay, essayeur du commerce, place Dau-
phine...  
2     [Dulay, chandronnier, r. du Pont- aux
Choux, 1...  
3     [Dufay (V.e), grenetière, r. du Faub.-S.
Denis...  
4     [Dufeu, charcutier, r. Montmartre, 89. 318, [T...  
...                                                 ...  
8440  [Lamarche, géographe , rue

In [8]:
gold_reference_valid = gold_reference[['brat','book']]
gold_reference_valid

brat  \
0     [Dufant (Victor), libraire, r. du Gros-Che-
ne...   
1     [Dufay, essayeur du commerce, place Dau-
phine...   
2     [Dulay, chandronnier, r. du Pont- aux
Choux, 1...   
3     [Dufay (V.e), grenetière, r. du Faub.-S.
Denis...   
4     [Dufeu, charcutier, r. Montmartre, 89. 318, [T...   
...                                                 ...   
8440  [Lamarche, géographe , rue du foin., [T0, PER,...   
8441  [Lamarck, membre de l'institut, quatrième muni...   
8442  [Lamare, notaire, rue du faubourg honoré., [T0...   
8443  [Lamarre , carrier, rue mouffetard., [T0, PER,...   
8444  [Lamarre, clerc de notaire, rue égalité., [T0,...   

                               book  
0                      Bottin1_1820  
1                      Bottin1_1820  
2                      Bottin1_1820  
3                      Bottin1_1820  
4                      Bottin1_1820  
...                             ...  
8440  Notables_communaux_seine_1801  
8441  Notables_communaux_seine_1801  
8442  Notables_communaux_seine_1801  
8443  Notables_communaux_seine_1801  
8444  Notables_communaux_seine_1801  

[8445 rows x 2 columns]

In [9]:
from dataset_util import train_dev_test_split, unwrap # Local imports
from sklearn.model_selection import train_test_split

# CONSTANTS
MIN_TRAINSET_SIZE = 30

 # Split 72/8/20% w. stratified sampling on directories names
train, dev, test = train_dev_test_split(gold_reference_valid.to_numpy())

# Iteratively split the trainset in half to create smaller trainsets
exp1_trainsets = [train]
t_len = len(train)

while True:
    try:
        current = exp1_trainsets[-1]
        _, groups = unwrap(current)
        smaller, rest = train_test_split(
            current,
            train_size=0.5,
            shuffle=True,
            random_state=config.SPLIT_SEED,
            stratify=groups,
        )
        t_len = len(rest)
        if t_len < MIN_TRAINSET_SIZE:
            break
        exp1_trainsets.append(smaller)

    except ValueError:
        # Stop now if we encounter the error "The least populated class in y has only 1 member".
        break

[len(s) for s in exp1_trainsets] # Should be 

[6084, 3042, 1521, 760, 380, 190, 95, 47]

In [10]:
# Sanity checks

# Dev set should contain 676 examples
assert len(dev) == 676

# Test set should contain 1685 examples
assert len(test) == 1685

# Lenghts of exp1_trainsets should be fixed
assert sorted([len(s) for s in exp1_trainsets] ) == sorted([6084, 3042, 1521, 760, 380, 190, 95, 47])

In [11]:
dev

array([[list(['Delarue (Mad.), institution, pass. Sandrié, 2.', ['T0', 'PER', 'Delarue (Mad.)', 0, 14], ['T1', 'ACT', 'institution', 16, 27], ['T2', 'SPAT', 'pass. Sandrié, 2', 29, 45], ['T3', 'LOC', 'pass. Sandrié', 29, 42], ['T4', 'CARDINAL', '2', 44, 45]]),
        'Bottin1_1837'],
       [list(['Primault, tabletterie, r. du Vert-Bois, 8.', ['T0', 'PER', 'Primault', 0, 8], ['T1', 'ACT', 'tabletterie', 10, 21], ['T2', 'SPAT', 'r. du Vert-Bois, 8', 23, 41], ['T3', 'LOC', 'r. du Vert-Bois', 23, 38], ['T4', 'CARDINAL', '8', 40, 41]]),
        'Deflandre_1829'],
       [list(['Chatré, vins, St-Dominique, 94.', ['T0', 'PER', 'Chatré', 0, 6], ['T1', 'ACT', 'vins', 8, 12], ['T2', 'SPAT', 'St-Dominique, 94', 14, 30], ['T3', 'LOC', 'St-Dominique', 14, 26], ['T4', 'CARDINAL', '94', 28, 30]]),
        'Didot_1841a'],
       ...,
       [list(['Barthelemy, rue Grange-Batellière , n.° 2, —du Montblanc.', ['T0', 'PER', 'Barthelemy', 0, 10], ['T1', 'SPAT', 'rue Grange-Batellière , n.° 2, —du Montbl

In [12]:
if CREATE_REF_IO:
    from util_io import save_dataset_io
    
    RES = OUT_BASE / f"m2-experiment_1_prepared_dataset_ref_io_{MODEL_NAME}"
    if not os.path.exists(RES):
        os.makedirs(RES)
    NAMES = ["train","dev","test"]
    
    for train in exp1_trainsets:
        datasets = [train, dev, test]
        save_dataset_io(RES, datasets, ["train","dev","test"], suffix=len(train))

2023-05-03 14:22:58.511803: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-05-03 14:23:06.314882: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2023-05-03 14:23:06.315186: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2023-05-03 14:23:06.315202: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nv

['PER', [0, 5]]
['ACT', [7, 25]]
['SPAT', [27, 46]]
['LOC', [27, 42]]
['CARDINAL', [44, 46]]
['I-PER', 'I-ACT', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 5], [7, 15], [15, 25], [27, 32], [32, 46], [27, 32], [32, 42], [44, 46]]
['PER', [0, 18]]
['SPAT', [20, 49]]
['LOC', [20, 45]]
['CARDINAL', [47, 49]]
['I-PER', 'I-PER', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 5], [5, 18], [20, 22], [22, 49], [20, 22], [22, 45], [47, 49]]
['PER', [0, 9]]
['ACT', [11, 19]]
['SPAT', [21, 50]]
['LOC', [21, 46]]
['CARDINAL', [48, 50]]
['I-PER', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 9], [11, 19], [21, 23], [23, 50], [21, 23], [23, 46], [48, 50]]
['PER', [0, 10]]
['ACT', [12, 51]]
['SPAT', [53, 74]]
['LOC', [53, 71]]
['CARDINAL', [73, 74]]
['I-PER', 'I-ACT', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 10], [12, 17], [17, 51], [53, 55], [55, 74], [53, 55], [55, 71], [73, 74]]
['PER', [0, 11]]
['ACT', [13, 17]]
['SPAT', 

['I-PER', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 6], [8, 15], [17, 22], [22, 35], [17, 22], [22, 31], [33, 35]]
['PER', [0, 7]]
['ACT', [9, 14]]
['SPAT', [16, 31]]
['LOC', [16, 28]]
['CARDINAL', [30, 31]]
['I-PER', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 7], [9, 14], [16, 22], [22, 31], [16, 22], [22, 28], [30, 31]]
['PER', [0, 6]]
['ACT', [8, 27]]
['SPAT', [29, 60]]
['LOC', [29, 56]]
['CARDINAL', [58, 60]]
['I-PER', 'I-ACT', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 6], [8, 14], [14, 27], [29, 31], [31, 60], [29, 31], [31, 56], [58, 60]]
['PER', [0, 16]]
['ACT', [18, 57]]
['SPAT', [59, 72]]
['LOC', [59, 67]]
['CARDINAL', [69, 72]]
['I-PER', 'I-PER', 'I-ACT', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 7], [7, 16], [18, 26], [26, 57], [59, 61], [61, 72], [59, 61], [61, 67], [69, 72]]
['PER', [0, 6]]
['ACT', [8, 18]]
['SPAT', [20, 32]]
['LOC', [20, 28]]
['CARDINAL', [30, 32]]
['I-PER', 'I-

['I-PER', 'I-PER', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 4], [4, 14], [16, 23], [25, 30], [30, 52], [25, 30], [30, 48], [50, 52]]
['PER', [0, 6]]
['SPAT', [8, 29]]
['LOC', [8, 25]]
['CARDINAL', [27, 29]]
['I-PER', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 6], [8, 10], [10, 29], [8, 10], [10, 25], [27, 29]]
['PER', [0, 9]]
['SPAT', [12, 44]]
['LOC', [12, 30]]
['CARDINAL', [32, 33]]
['LOC', [35, 44]]
['I-PER', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL', 'I-LOC'] [[0, 9], [12, 13], [13, 44], [12, 13], [13, 30], [32, 33], [35, 44]]
['PER', [0, 12]]
['ACT', [14, 27]]
['SPAT', [29, 45]]
['LOC', [29, 42]]
['CARDINAL', [44, 45]]
['I-PER', 'I-PER', 'I-ACT', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 7], [7, 12], [14, 18], [18, 27], [29, 32], [32, 45], [29, 32], [32, 42], [44, 45]]
['PER', [0, 8]]
['ACT', [10, 19]]
['SPAT', [21, 40]]
['LOC', [21, 35]]
['CARDINAL', [37, 40]]
['I-PER', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', '

['I-PER', 'I-ACT', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-CARDINAL', 'I-CARDINAL'] [[0, 5], [7, 12], [12, 22], [24, 29], [29, 38], [24, 29], [31, 33], [33, 38]]
['PER', [0, 6]]
['SPAT', [8, 34]]
['LOC', [8, 20]]
['CARDINAL', [22, 25]]
['LOC', [29, 34]]
['I-PER', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL', 'I-LOC'] [[0, 6], [8, 10], [10, 34], [8, 10], [10, 20], [22, 25], [29, 34]]
['PER', [0, 8]]
['ACT', [10, 15]]
['SPAT', [16, 36]]
['LOC', [16, 32]]
['CARDINAL', [34, 36]]
['I-PER', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 8], [10, 15], [16, 24], [24, 36], [16, 24], [24, 32], [34, 36]]
['PER', [0, 6]]
['ACT', [8, 16]]
['SPAT', [18, 41]]
['LOC', [18, 37]]
['CARDINAL', [39, 41]]
['I-PER', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 6], [8, 16], [18, 23], [23, 41], [18, 23], [23, 37], [39, 41]]
['PER', [0, 8]]
['ACT', [10, 33]]
['SPAT', [35, 54]]
['LOC', [35, 50]]
['CARDINAL', [52, 54]]
['I-PER', 'I-ACT', 'I-ACT', 'I-SPAT', 'I-SPAT',

...

['I-PER', 'I-PER', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 7], [7, 15], [16, 18], [18, 33], [16, 18], [18, 29], [31, 33]]
['PER', [0, 15]]
['SPAT', [16, 40]]
['LOC', [16, 35]]
['CARDINAL', [37, 40]]
['I-PER', 'I-PER', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 7], [7, 15], [16, 21], [21, 40], [16, 21], [21, 35], [37, 40]]
['PER', [0, 25]]
['SPAT', [26, 57]]
['LOC', [26, 53]]
['CARDINAL', [55, 57]]
['I-PER', 'I-PER', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 10], [10, 25], [26, 28], [28, 57], [26, 28], [28, 53], [55, 57]]
['PER', [0, 16]]
['SPAT', [17, 36]]
['LOC', [17, 32]]
['CARDINAL', [34, 36]]
['I-PER', 'I-PER', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 8], [8, 16], [17, 21], [21, 36], [17, 21], [21, 32], [34, 36]]
['PER', [0, 30]]
['ACT', [31, 83]]
['SPAT', [85, 111]]
['LOC', [85, 106]]
['CARDINAL', [108, 110]]
['I-PER', 'I-PER', 'I-ACT', 'I-ACT', 'I-SPAT', 'I-SPAT', 'I-LOC', 'I-LOC', 'I-CARDINAL'] [[0, 8], [8, 30], [31, 

  0%|          | 0/2 [00:00<?, ?ba/s]

Saving the dataset (0/1 shards):   0%|          | 0/47 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/676 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/1685 [00:00<?, ? examples/s]

In [ ]:
if CREATE_REF_IOB2:
    from util_iob2 import save_dataset_iob2
    
    RES = OUT_BASE / f"m2-experiment_1_prepared_dataset_ref_iob2_{MODEL_NAME}_v2"
    if not os.path.exists(RES):
        os.makedirs(RES)
    NAMES = ["train","dev","test"]
    
    for train in exp1_trainsets:
        datasets = [train, dev, test]
        save_dataset_iob2(RES, datasets, ["train","dev","test"], suffix=len(train))

## 01.2 Noisy data

In [ ]:
#Sanity check
PATH = DATASETS / "61-ner_align_pero_brat/"
f = open(f"{PATH}/all_brat.json")
data = json.load(f)
f.close()

In [ ]:
gold_reference = pd.DataFrame.from_records(data)
gold_reference

In [ ]:
gold_reference_valid = gold_reference.loc[gold_reference['has_valid_ner_xml'] == True]
gold_reference_valid = gold_reference_valid[['brat','book']]
gold_reference_valid

### Create subsets

In [ ]:
from dataset_util import train_dev_test_split, unwrap # Local imports
from sklearn.model_selection import train_test_split

# CONSTANTS
MIN_TRAINSET_SIZE = 30

 # Split 72/8/20% w. stratified sampling on directories names
train, dev, test = train_dev_test_split(gold_reference_valid.to_numpy())

# Iteratively split the trainset in half to create smaller trainsets
exp1_trainsets = [train]
t_len = len(train)

while True:
    try:
        current = exp1_trainsets[-1]
        _, groups = unwrap(current)
        smaller, rest = train_test_split(
            current,
            train_size=0.5,
            shuffle=True,
            random_state=config.SPLIT_SEED,
            stratify=groups,
        )
        t_len = len(rest)
        if t_len < MIN_TRAINSET_SIZE:
            break
        exp1_trainsets.append(smaller)

    except ValueError:
        # Stop now if we encounter the error "The least populated class in y has only 1 member".
        break

[len(s) for s in exp1_trainsets] # Should be 

In [ ]:
# Sanity checks

# Dev set should contain 676 examples
assert len(dev) == 676

# Test set should contain 1685 examples
assert len(test) == 1685

# Lenghts of exp1_trainsets should be fixed
assert sorted([len(s) for s in exp1_trainsets] ) == sorted([6084, 3042, 1521, 760, 380, 190, 95, 47])

In [ ]:
if CREATE_PERO_IO:
    from util_io import save_dataset_io
    
    RES = OUT_BASE / f"m2-experiment_2_prepared_dataset_pero_ocr_io_{MODEL_NAME}"
    if not os.path.exists(RES):
        os.makedirs(RES)
    NAMES = ["train","dev","test"]
    
    for train in exp1_trainsets:
        datasets = [train, dev, test]
        save_dataset_io(RES, datasets, ["train","dev","test"], suffix=len(train))

In [ ]:
if CREATE_PERO_IOB2:
    from util_iob2 import save_dataset_iob2
    
    RES = OUT_BASE / f"m2-experiment_2_prepared_dataset_pero_ocr_iob2_{MODEL_NAME}_v2"
    if not os.path.exists(RES):
        os.makedirs(RES)
    NAMES = ["train","dev","test"]
    
    for train in exp1_trainsets:
        datasets = [train, dev, test]
        save_dataset_iob2(RES, datasets, ["train","dev","test"], suffix=len(train))

In [ ]:
from datasets import load_from_disk
set_ = load_from_disk(OUT_BASE / f"m2-experiment_2_prepared_dataset_pero_ocr_iob2_{MODEL_NAME}_v2/huggingface_6084")

In [ ]:
set_["test"][0]